# Autoscaling a SageMaker Endpoint

In [7]:
import boto3
import sagemaker
import pandas as pd

sess   = sagemaker.Session()
bucket = sess.default_bucket()
role = sagemaker.get_execution_role()
region = boto3.Session().region_name

sm = boto3.Session().client(service_name='sagemaker', region_name=region)
autoscale = boto3.Session().client(service_name='application-autoscaling', region_name=region)

In [2]:
%store -r tensorflow_endpoint_name 

no stored variable or alias tensorflow_endpoint_name


In [4]:
try:
    tensorflow_endpoint_name
    print('[OK]')
except NameError:
    print('+++++++++++++++++++++++++++++++')
    print('[ERROR] Please run the notebooks in the previous notebook before you continue.')
    print('+++++++++++++++++++++++++++++++')

[OK]


In [5]:
print(tensorflow_endpoint_name)

tensorflow-training-201129-2249-002-19a0db08-tf-1606694592


# Copy the Model to the Notebook

In [8]:
autoscale.register_scalable_target(
    ServiceNamespace='sagemaker',
    ResourceId="endpoint/" + tensorflow_endpoint_name + "/variant/AllTraffic",
    ScalableDimension='sagemaker:variant:DesiredInstanceCount',
    MinCapacity=1,
    MaxCapacity=2,
    RoleARN=role,
    SuspendedState={
        'DynamicScalingInSuspended': False,
        'DynamicScalingOutSuspended': False,
        'ScheduledScalingSuspended': False
    }
)


{'ResponseMetadata': {'RequestId': '2537e452-2c22-4578-83f6-4f40ec4df153',
  'HTTPStatusCode': 200,
  'HTTPHeaders': {'x-amzn-requestid': '2537e452-2c22-4578-83f6-4f40ec4df153',
   'content-type': 'application/x-amz-json-1.1',
   'content-length': '2',
   'date': 'Wed, 16 Dec 2020 01:22:14 GMT'},
  'RetryAttempts': 0}}

In [9]:
# check the target is available
autoscale.describe_scalable_targets(
    ServiceNamespace='sagemaker',
    MaxResults=100,
)

{'ScalableTargets': [{'ServiceNamespace': 'sagemaker',
   'ResourceId': 'endpoint/tensorflow-training-201129-2249-002-19a0db08-tf-1606694592/variant/AllTraffic',
   'ScalableDimension': 'sagemaker:variant:DesiredInstanceCount',
   'MinCapacity': 1,
   'MaxCapacity': 2,
   'RoleARN': 'arn:aws:iam::835319576252:role/aws-service-role/sagemaker.application-autoscaling.amazonaws.com/AWSServiceRoleForApplicationAutoScaling_SageMakerEndpoint',
   'CreationTime': datetime.datetime(2020, 12, 16, 1, 22, 14, 574000, tzinfo=tzlocal()),
   'SuspendedState': {'DynamicScalingInSuspended': False,
    'DynamicScalingOutSuspended': False,
    'ScheduledScalingSuspended': False}}],
 'ResponseMetadata': {'RequestId': 'bc38f7f6-4d6c-4df0-b4e6-808967187707',
  'HTTPStatusCode': 200,
  'HTTPHeaders': {'x-amzn-requestid': 'bc38f7f6-4d6c-4df0-b4e6-808967187707',
   'content-type': 'application/x-amz-json-1.1',
   'content-length': '569',
   'date': 'Wed, 16 Dec 2020 01:22:39 GMT'},
  'RetryAttempts': 0}}

In [10]:
autoscale.put_scaling_policy(
    PolicyName='bert-reviews-autoscale-policy',
    ServiceNamespace='sagemaker',
    ResourceId="endpoint/" + tensorflow_endpoint_name + "/variant/AllTraffic",
    ScalableDimension='sagemaker:variant:DesiredInstanceCount',
    PolicyType='TargetTrackingScaling',
    TargetTrackingScalingPolicyConfiguration={
        'TargetValue': 2.0,
        'PredefinedMetricSpecification': {
            'PredefinedMetricType': 'SageMakerVariantInvocationsPerInstance',
        },
        'ScaleOutCooldown': 60,
        'ScaleInCooldown': 300,
    }
)

{'PolicyARN': 'arn:aws:autoscaling:us-east-1:835319576252:scalingPolicy:3ccb62de-fd2e-4825-b0bc-048eeb1ad698:resource/sagemaker/endpoint/tensorflow-training-201129-2249-002-19a0db08-tf-1606694592/variant/AllTraffic:policyName/bert-reviews-autoscale-policy',
 'Alarms': [{'AlarmName': 'TargetTracking-endpoint/tensorflow-training-201129-2249-002-19a0db08-tf-1606694592/variant/AllTraffic-AlarmHigh-807b22b1-d210-431c-826d-83f79f317484',
   'AlarmARN': 'arn:aws:cloudwatch:us-east-1:835319576252:alarm:TargetTracking-endpoint/tensorflow-training-201129-2249-002-19a0db08-tf-1606694592/variant/AllTraffic-AlarmHigh-807b22b1-d210-431c-826d-83f79f317484'},
  {'AlarmName': 'TargetTracking-endpoint/tensorflow-training-201129-2249-002-19a0db08-tf-1606694592/variant/AllTraffic-AlarmLow-6ed070aa-3f9e-41ca-91a4-06ea1b22c193',
   'AlarmARN': 'arn:aws:cloudwatch:us-east-1:835319576252:alarm:TargetTracking-endpoint/tensorflow-training-201129-2249-002-19a0db08-tf-1606694592/variant/AllTraffic-AlarmLow-6ed070

In [11]:
from IPython.core.display import display, HTML

display(HTML('<b>Review <a target="blank" href="https://console.aws.amazon.com/sagemaker/home?region={}#/endpoints/{}">SageMaker REST Endpoint</a></b>'.format(region, tensorflow_endpoint_name)))


# Test the Deployed Model

In [13]:
import json
from sagemaker.tensorflow.model import TensorFlowPredictor

predictor = TensorFlowPredictor(endpoint_name=tensorflow_endpoint_name,
                                sagemaker_session=sess,
                                model_name='saved_model',
                                model_version=0)

### Waiting for the Endpoint to be ready to Serve Predictions

In [ ]:
import time

time.sleep(30)

# Predict the `star_rating` with Ad Hoc `review_body` Samples

In [36]:
reviews = ["This is great!"]

for i in range(0, 100000):
    predicted_classes = predictor.predict(reviews)

    for predicted_class, review in zip(predicted_classes, reviews):
        print('[Predicted Star Rating: {}]'.format(predicted_class), review)

[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted S

[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted S

[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted S

[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted S

[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted S

...

[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted S

[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted S

[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted S

[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted S

[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted Star Rating: predictions] This is great!
[Predicted S

# Predict the `star_rating` with `review_body` Samples from our TSV's

In [ ]:
import csv

df_reviews = pd.read_csv('./data/amazon_reviews_us_Digital_Software_v1_00.tsv.gz', 
                         delimiter='\t', 
                         quoting=csv.QUOTE_NONE,
                         compression='gzip')
df_sample_reviews = df_reviews[['review_body', 'star_rating']].sample(n=100)
df_sample_reviews = df_sample_reviews.reset_index()
df_sample_reviews.shape

In [ ]:
import pandas as pd

def predict(review_body):
    return predictor.predict(review_body)

df_sample_reviews['predicted_class'] = df_sample_reviews['review_body'].map(predict)
df_sample_reviews.head(5)

# Delete Endpoint
To save cost, we should delete the endpoint.

In [ ]:
# sm.delete_endpoint(
#      EndpointName=tensorflow_endpoint_name
# )

In [ ]:
%%javascript
Jupyter.notebook.save_checkpoint();
Jupyter.notebook.session.delete();